In [1]:
import Downloads

In [2]:
using SHA

In [3]:
git_zip = "git_web_ml.zip"

if !isfile(git_zip)
   Downloads.download("https://snap.stanford.edu/data/" * "git_web_ml.zip", git_zip)
end

"git_web_ml.zip"

In [4]:
isfile(git_zip)

true

In [5]:
open(sha256, git_zip) == [0x56, 0xc0, 0xc1, 0xc2,
                                 0xc4, 0x60, 0xdc, 0x4c,
                                 0x7b, 0xf8, 0x93, 0x57,
                                 0xb1, 0xfe, 0xc0, 0x20,
                                 0xf4, 0x5e, 0x2e, 0xce,
                                 0xba, 0xb8, 0x1d, 0x13,
                                 0x1d, 0x07, 0x3b, 0x10,
                                 0xe2, 0x8e, 0xc0, 0x31]

true

In [7]:
import Pkg; Pkg.add("ZipFile")

    Updating registry at `~/.julia/registries/General.toml`
   Resolving package versions...
   Installed ZipFile ─ v0.10.1
    Updating `~/.julia/environments/v1.8/Project.toml`
  [a5390f91] + ZipFile v0.10.1
    Updating `~/.julia/environments/v1.8/Manifest.toml`
  [a5390f91] + ZipFile v0.10.1
Precompiling project...
  ✓ ZipFile
  1 dependency successfully precompiled in 1 seconds. 206 already precompiled.


In [8]:
import ZipFile

In [9]:
git_archive = ZipFile.Reader(git_zip)

ZipFile.Reader for IOStream(<file git_web_ml.zip>) containing 6 files:

uncompressedsize method  mtime            name
----------------------------------------------
               0 Store   2019-10-03 21-49 git_web_ml/
         3306139 Deflate 2019-09-20 22-39 git_web_ml/musae_git_edges.csv
         4380176 Deflate 2019-09-20 22-39 git_web_ml/musae_git_features.json
          676528 Deflate 2019-09-20 22-39 git_web_ml/musae_git_target.csv
             485 Deflate 2019-10-03 21-44 git_web_ml/citing.txt
             881 Deflate 2019-10-03 21-49 git_web_ml/README.txt


In [10]:
git_archive.files

6-element Vector{ZipFile.ReadableFile}:
 ZipFile.ReadableFile(name=git_web_ml/, method=Store, uncompresssedsize=0, compressedsize=0, mtime=1.57013574e9)
 ZipFile.ReadableFile(name=git_web_ml/musae_git_edges.csv, method=Deflate, uncompresssedsize=3306139, compressedsize=1089598, mtime=1.569015584e9)
 ZipFile.ReadableFile(name=git_web_ml/musae_git_features.json, method=Deflate, uncompresssedsize=4380176, compressedsize=961155, mtime=1.569015584e9)
 ZipFile.ReadableFile(name=git_web_ml/musae_git_target.csv, method=Deflate, uncompresssedsize=676528, compressedsize=343259, mtime=1.569015584e9)
 ZipFile.ReadableFile(name=git_web_ml/citing.txt, method=Deflate, uncompresssedsize=485, compressedsize=302, mtime=1.57013548e9)
 ZipFile.ReadableFile(name=git_web_ml/README.txt, method=Deflate, uncompresssedsize=881, compressedsize=479, mtime=1.57013574e9)

In [11]:
git_archive.files[2].name

"git_web_ml/musae_git_edges.csv"

In [12]:
function ingest_to_df(archive::ZipFile.Reader, filename::AbstractString) idx = only(findall(x -> x.name == filename, archive.files))
    return CSV.read(read(archive.files[idx]), DataFrame)
end

ingest_to_df (generic function with 1 method)

In [13]:
findall(x -> x.name == "git_web_ml/musae_git_edges.csv", git_archive.files)

1-element Vector{Int64}:
 2

In [14]:
using CSV

In [15]:
using DataFrames

In [16]:
edges_df = ingest_to_df(git_archive, "git_web_ml/musae_git_edges.csv");

In [17]:
classes_df = ingest_to_df(git_archive, "git_web_ml/musae_git_target.csv");

In [18]:
close(git_archive)

In [27]:
edges_df[1:4, :]

4×2 DataFrame
 Row │ id_1   id_2  
     │ Int64  Int64 
─────┼──────────────
   1 │     0  23977
   2 │     1  34526
   3 │     1   2370
   4 │     1  14683

In [19]:
summary(edges_df)

"289003×2 DataFrame"

In [20]:
summary(classes_df)

"37700×3 DataFrame"

In [21]:
describe(classes_df, :min, :max, :mean, :nmissing, :eltype)

3×6 DataFrame
 Row │ variable   min            max      mean      nmissing  eltype   
     │ Symbol     Any            Any      Union…    Int64     DataType 
─────┼─────────────────────────────────────────────────────────────────
   1 │ id         0              37699    18849.5          0  Int64
   2 │ name       007arunwilson  timqian                   0  String31
   3 │ ml_target  0              1        0.258329         0  Int64

> An important feature we learn from listing 12.3 is that the developer’s identifier (col- umns id_1 and id_2 in edges_df and column id in classes_df) starts indexing with 0. Let’s increase all the indices by 1 so that they start from 1. This is needed because in section 12.2, we will use these edges to create a graph with the Graphs.jl

In [22]:
classes_df.id .+= 1

37700-element Vector{Int64}:
     1
     2
     3
     4
     5
     6
     7
     8
     9
    10
    11
    12
    13
     ⋮
 37689
 37690
 37691
 37692
 37693
 37694
 37695
 37696
 37697
 37698
 37699
 37700

In [28]:
edges_df .+= 1

289003×2 DataFrame
    Row │ id_1   id_2  
        │ Int64  Int64 
────────┼──────────────
      1 │     1  23978
      2 │     2  34527
      3 │     2   2371
      4 │     2  14684
      5 │     2  29983
      6 │     2  21143
      7 │     2  20364
      8 │     2  23831
      9 │     2  34036
     10 │  6068  19721
     11 │  6068  20184
   ⋮    │   ⋮      ⋮
 288994 │ 37495  37578
 288995 │ 37496  18378
 288996 │ 31256  37603
 288997 │ 37520  37679
 288998 │ 19094   2348
 288999 │ 37528  37597
 289000 │ 37530  37602
 289001 │ 37645   2348
 289002 │ 25880   2348
 289003 │ 25617   2348
    288982 rows omitted

In [23]:
classes_df[1:3,:]

3×3 DataFrame
 Row │ id     name         ml_target 
     │ Int64  String31     Int64     
─────┼───────────────────────────────
   1 │     1  Eiryyy               0
   2 │     2  shawflying           0
   3 │     3  JpMCarrilho          1

> A rule to remember is that broadcasting data frames works in the same way as for other arrays. Therefore, everything that you learned about broadcasting in Julia in general (covered in chapter 5) applies to data frame objects.

# Graphs.jl

In [25]:
import Pkg; Pkg.add("Graphs")

   Resolving package versions...
   Installed ArnoldiMethod ─ v0.2.0
   Installed Inflate ─────── v0.1.3
   Installed SimpleTraits ── v0.9.4
   Installed Graphs ──────── v1.8.0
    Updating `~/.julia/environments/v1.8/Project.toml`
  [86223c79] + Graphs v1.8.0
    Updating `~/.julia/environments/v1.8/Manifest.toml`
  [ec485272] + ArnoldiMethod v0.2.0
  [86223c79] + Graphs v1.8.0
  [d25df0c9] + Inflate v0.1.3
  [699a6c99] + SimpleTraits v0.9.4
  [8ba89e20] + Distributed
  [1a1011a3] + SharedArrays
Precompiling project...
  ✓ Inflate
  ✓ SimpleTraits
  ✓ ArnoldiMethod
  ✓ Graphs
  4 dependencies successfully precompiled in 3 seconds. 207 already precompiled.


In [26]:
using Graphs

In [29]:
gh = SimpleGraph(nrow(classes_df))

{37700, 0} undirected simple Int64 graph

In [30]:
for (srt, dst) in eachrow(edges_df)
    add_edge!(gh, srt, dst)
end

In [31]:
gh

{37700, 289003} undirected simple Int64 graph

In [32]:
nv(gh)

37700

In [33]:
ne(gh)

289003

In [34]:
degree(gh)

37700-element Vector{Int64}:
   1
   8
   1
   5
   2
   1
   6
   8
   8
   7
  66
   2
   6
   ⋮
   8
   9
 215
   3
  58
   4
  20
   1
   2
   4
   3
   4

Easily add to dataframes...

In [37]:
classes_df.deg = degree(gh)

37700-element Vector{Int64}:
   1
   8
   1
   5
   2
   1
   6
   8
   8
   7
  66
   2
   6
   ⋮
   8
   9
 215
   3
  58
   4
  20
   1
   2
   4
   3
   4

In [38]:
classes_df

37700×4 DataFrame
   Row │ id     name               ml_target  deg   
       │ Int64  String31           Int64      Int64 
───────┼────────────────────────────────────────────
     1 │     1  Eiryyy                     0      1
     2 │     2  shawflying                 0      8
     3 │     3  JpMCarrilho                1      1
     4 │     4  SuhwanCha                  0      5
     5 │     5  sunilangadi2               1      2
     6 │     6  j6montoya                  0      1
     7 │     7  sfate                      0      6
     8 │     8  amituuush                  0      8
     9 │     9  mauroherlein               0      8
    10 │    10  ParadoxZero                0      7
    11 │    11  llazzaro                   0     66
   ⋮   │   ⋮            ⋮              ⋮        ⋮
 37691 │ 37691  tbranyen                   0    215
 37692 │ 37692  bblu                       0      3
 37693 │ 37693  mubaris                    0     58
 37694 │ 37694  chengzhongkai              1      4
 37695 │ 37695  alFReD-NSH                 0     20
 37696 │ 37696  shawnwanderson             1      1
 37697 │ 37697  kris-ipeh                  0      2
 37698 │ 37698  qpautrat                   0      4
 37699 │ 37699  Injabie3                   1      3
 37700 │ 37700  caseycavanagh              0      4
                                  37679 rows omitted

This seemed fast... iterate over all the edges, assigning to the vertices (classes) df

In [39]:
function deg_class(gh, class)
    deg_ml = zeros(Int, length(class))
    deg_web = zeros(Int, length(class))
    for edge in edges(gh)
        a, b = edge.src, edge.dst
        if class[b] == 1
            deg_ml[a] += 1
        else
            deg_web[a] += 1
        end
        if class[a] == 1
            deg_ml[b] += 1
        else
            deg_web[b] += 1
        end 
    end
    return (deg_ml, deg_web)
end

deg_class (generic function with 1 method)

In [40]:
classes_df.deg_ml, classes_df.deg_web = deg_class(gh, classes_df.ml_target)

([0, 0, 0, 3, 1, 0, 0, 0, 1, 2  …  2, 0, 12, 1, 0, 1, 0, 0, 1, 0], [1, 8, 1, 2, 1, 1, 6, 8, 7, 5  …  213, 3, 46, 3, 20, 0, 2, 4, 2, 4])

In [41]:
classes_df

37700×6 DataFrame
   Row │ id     name               ml_target  deg    deg_ml  deg_web 
       │ Int64  String31           Int64      Int64  Int64   Int64   
───────┼─────────────────────────────────────────────────────────────
     1 │     1  Eiryyy                     0      1       0        1
     2 │     2  shawflying                 0      8       0        8
     3 │     3  JpMCarrilho                1      1       0        1
     4 │     4  SuhwanCha                  0      5       3        2
     5 │     5  sunilangadi2               1      2       1        1
     6 │     6  j6montoya                  0      1       0        1
     7 │     7  sfate                      0      6       0        6
     8 │     8  amituuush                  0      8       0        8
     9 │     9  mauroherlein               0      8       1        7
    10 │    10  ParadoxZero                0      7       2        5
    11 │    11  llazzaro                   0     66      13       53
   ⋮   │   ⋮            ⋮              ⋮        ⋮      ⋮        ⋮
 37691 │ 37691  tbranyen                   0    215       2      213
 37692 │ 37692  bblu                       0      3       0        3
 37693 │ 37693  mubaris                    0     58      12       46
 37694 │ 37694  chengzhongkai              1      4       1        3
 37695 │ 37695  alFReD-NSH                 0     20       0       20
 37696 │ 37696  shawnwanderson             1      1       1        0
 37697 │ 37697  kris-ipeh                  0      2       0        2
 37698 │ 37698  qpautrat                   0      4       0        4
 37699 │ 37699  Injabie3                   1      3       1        2
 37700 │ 37700  caseycavanagh              0      4       0        4
                                                   37679 rows omitted

In [42]:
describe(classes_df, :min, :max, :mean, :std)

6×5 DataFrame
 Row │ variable   min            max      mean      std      
     │ Symbol     Any            Any      Union…    Union…   
─────┼───────────────────────────────────────────────────────
   1 │ id         1              37700    18850.5   10883.2
   2 │ name       007arunwilson  timqian                     
   3 │ ml_target  0              1        0.258329  0.437722
   4 │ deg        1              9458     15.3317   80.7881
   5 │ deg_ml     0              1620     2.22981   13.935
   6 │ deg_web    0              8194     13.1019   69.9712

In [43]:
using Statistics


In [44]:
for type in [0, 1], col in ["deg_ml", "deg_web"]
  println((type, col, mean(classes_df[classes_df.ml_target .== type, col])))
end

(0, "deg_ml", 1.5985122134401488)
(0, "deg_web", 16.066878866993314)
(1, "deg_ml", 4.042304138001848)
(1, "deg_web", 4.589382893520895)


> We see that web developers (encoded by 0) have many more web friends than machine learning friends on average.

## split-apply-combine pattern 

use two functions:
* groupby—Splits a data frame; you learned about this function in chapter 11
* combine—Takes a GroupedDataFrame object and performs its aggregation


![](./combine-ops.png)

In [48]:
gdf = groupby(classes_df, :ml_target)

GroupedDataFrame with 2 groups based on key: ml_target
First Group (27961 rows): ml_target = 0
   Row │ id     name           ml_target  deg    deg_ml  deg_web 
       │ Int64  String31       Int64      Int64  Int64   Int64   
───────┼─────────────────────────────────────────────────────────
     1 │     1  Eiryyy                 0      1       0        1
     2 │     2  shawflying             0      8       0        8
     3 │     4  SuhwanCha              0      5       3        2
     4 │     6  j6montoya              0      1       0        1
   ⋮   │   ⋮          ⋮            ⋮        ⋮      ⋮        ⋮
 27959 │ 37697  kris-ipeh              0      2       0        2
 27960 │ 37698  qpautrat               0      4       0        4
 27961 │ 37700  caseycavanagh          0      4       0        4
                                               27954 rows omitted
⋮
Last Group (9739 rows): ml_target = 1
  Row │ id     name            ml_target  deg    deg_ml  deg_web 
      │ Int64  String31        Int64      Int64  Int64   Int64   
──────┼──────────────────────────────────────────────────────────
    1 │     3  JpMCarrilho             1      1       0        1
    2 │     5  sunilangadi2            1      2       1        1
    3 │    33  city292                 1      2       2        0
  ⋮   │   ⋮          ⋮             ⋮        ⋮      ⋮        ⋮
 9737 │ 37694  chengzhongkai           1      4       1        3
 9738 │ 37696  shawnwanderson          1      1       1        0
 9739 │ 37699  Injabie3                1      3       1        2
                                                9733 rows omitted

In [47]:
combine(gdf, :deg_ml => mean => :mean_deg_ml, :deg_web => mean => :mean_deg_web)


2×3 DataFrame
 Row │ ml_target  mean_deg_ml  mean_deg_web 
     │ Int64      Float64      Float64      
─────┼──────────────────────────────────────
   1 │         0      1.59851      16.0669
   2 │         1      4.0423        4.58938

In [49]:
using Plots

In [50]:
scatter(classes_df.deg_ml, classes_df.deg_web;
                       color=[x == 1 ? "black" : "yellow"
                              for x in classes_df.ml_target],
                       xlabel="degree ml", ylabel="degree web", labels=false)

Book goes on to do some transformations, fit to model, give more details on data frame mutations